# Cluster Analysis

In [ ]:
# Clustering test script for short static task
# Script by Branden J. Bio

import csv
import pandas as pd
import numpy as np
import scipy as sp
import statistics
from scipy import stats
import seaborn as sns
import matplotlib.pyplot as plt
from pathlib import Path
from mpl_toolkits.mplot3d import Axes3D
from sklearn import metrics
from sklearn.cluster import KMeans
import matplotlib.cm as cm
from statsmodels.stats import weightstats as stests
from statsmodels.formula.api import ols
pd.set_option('display.max_rows', 2000)

import statsmodels.api as sm
from statsmodels.nonparametric.smoothers_lowess import lowess

## Setup

In [ ]:
# Raw data filename
fn1 = "processed_data1.xlsx"
fn2 = "processed_data2.xlsx"

# Import data csv
df1_raw = pd.read_excel(fn1,sheet_name="data",usecols="A:IF")
df2_raw = pd.read_excel(fn2,sheet_name="SSAT",usecols="A:IF")
rmet1_raw = pd.read_excel(fn1,sheet_name="rmet",usecols="A")
rmet2_raw = pd.read_excel(fn2,sheet_name="RMET",usecols="A")
ht_raw = pd.read_excel(fn2,sheet_name="HT")
hte_raw = pd.read_excel(fn2,sheet_name="HT_WC1",usecols="A:B")

# Copy raw data to manipulate
df_temp = pd.concat([df1_raw,df2_raw],axis=0)
df_temp = df_temp.reset_index(drop=True)
rmet_temp = pd.concat([rmet1_raw,rmet2_raw],axis=0)
rmet_temp = rmet_temp.reset_index(drop=True)
ht_pretemp = pd.concat([ht_raw,hte_raw],axis=1)

naDiff = pd.to_numeric(rmet_temp.shape[0] - ht_pretemp.shape[0])

df_na = pd.DataFrame(np.nan, index=range(0,naDiff), columns=['ht','ht_eval','WC_Avg'])

ht_temp = pd.concat([df_na,ht_pretemp],axis=0)
ht_temp = ht_temp.reset_index(drop=True)

# Copy raw data to manipulate
combined = pd.concat([df_temp,rmet_temp,ht_temp],axis=1)
combined = combined.reset_index(drop=True)

In [ ]:
# Create subject list
subs = []

# Count subs
subCount = len(combined.index)

for x in range(1,subCount + 1):
    if x < 10:
        tmp = "s00" + str(x)
    elif 9 < x < 100:
        tmp = "s0" + str(x)
    elif x > 99: 
        tmp = "s" + str(x)
    subs.append(tmp)

# Add column with subject names
combined.insert(loc=0, column='sub', value=subs)

In [ ]:
exclSub2 = combined[ combined['ht_eval'] == 0 ].index
combined.drop(exclSub2, inplace=True)
exclSub3 = combined[ combined['ht'] == "na" ].index
combined.drop(exclSub3, inplace=True)
combined.shape

In [ ]:
# drop subs under 80% performance
thresh80 = combined.dropna(thresh=195)

# Replace df with thresholded subs
ssat = thresh80.iloc[:,0:241]

# Reset indices (row names) to make up for dropped subs
df = ssat.reset_index(drop=True)

# Pull out rmet from joint df
rmet = thresh80[['rmet']]

# Reset indices (row names) to make up for dropped subs
rmet = rmet.reset_index(drop=True)

# Pull out ht from joint df
ht = thresh80[['ht']]

# Reset indices (row names) to make up for dropped subs
ht = ht.reset_index(drop=True)

hte = thresh80.iloc[:,242:245]
hte = hte.reset_index(drop=True)

In [ ]:
na2_list = thresh80.isna().sum(axis=1)
nadf = pd.DataFrame(na2_list)
nadf.columns = ["NAs"]

In [ ]:
# Subset data into fine grain categories
AAN = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_AAC")]],axis=1)
AAP = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_AAI")]],axis=1)
AHN = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_HAI")]],axis=1)
AHP = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_HAC")]],axis=1)
TAN = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_ATC")]],axis=1)
TAP = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_ATI")]],axis=1)
THN = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_HTI")]],axis=1)
THP = pd.concat([df.iloc[:,0:1],df.loc[:,df.columns.str.contains("_HTC")]],axis=1)

# Subset data into 4 main categories & create long-form versions of dfs
GNegENeg = pd.merge(AAP, AHN, on='sub')
GNegENeg.insert(loc=1, column='cond', value='GNegENeg')
GNegENeg_melted = pd.melt(GNegENeg,('sub','cond'),var_name='trial',value_name='rating')
GNegEPos = pd.merge(AAN, AHP, on='sub')
GNegEPos.insert(loc=1, column='cond', value='GNegEPos')
GNegEPos_melted = pd.melt(GNegEPos,('sub','cond'),var_name='trial',value_name='rating')
GPosENeg = pd.merge(TAP, THN, on='sub')
GPosENeg.insert(loc=1, column='cond', value='GPosENeg')
GPosENeg_melted = pd.melt(GPosENeg,('sub','cond'),var_name='trial',value_name='rating')
GPosEPos = pd.merge(TAN, THP, on='sub')
GPosEPos.insert(loc=1, column='cond', value='GPosEPos')
GPosEPos_melted = pd.melt(GPosEPos,('sub','cond'),var_name='trial',value_name='rating')

# Combine all conditions into one dataframe to plot
AllConds = pd.concat([GNegENeg_melted,GNegEPos_melted,GPosENeg_melted,GPosEPos_melted])

# Create numerical value dataframe
GnEn = GNegENeg.replace({'Not Aware':-1,'Somewhat Aware':0,'Very Aware':1})
GnEp = GNegEPos.replace({'Not Aware':-1,'Somewhat Aware':0,'Very Aware':1})
GpEn = GPosENeg.replace({'Not Aware':-1,'Somewhat Aware':0,'Very Aware':1})
GpEp = GPosEPos.replace({'Not Aware':-1,'Somewhat Aware':0,'Very Aware':1})
GnEn_sums = GnEn.sum(axis=1)
GnEp_sums = GnEp.sum(axis=1)
GpEn_sums = GpEn.sum(axis=1)
GpEp_sums = GpEp.sum(axis=1)
GnEn_means = GnEn.mean(axis=1)
GnEp_means = GnEp.mean(axis=1)
GpEn_means = GpEn.mean(axis=1)
GpEp_means = GpEp.mean(axis=1)

condSums = pd.DataFrame(columns=['GnEn', 'GnEp', 'GpEn', 'GpEp'])
condMeans = pd.DataFrame(columns=['GnEn', 'GnEp', 'GpEn', 'GpEp'])
subNum = len(df.index)

for n in range(1,subNum + 1):
    rowNum = n - 1
    a = GnEn_sums.iloc[rowNum]
    b = GnEp_sums.iloc[rowNum]
    c = GpEn_sums.iloc[rowNum]
    d = GpEp_sums.iloc[rowNum]
    condSums = condSums.append({'GnEn': a, 'GnEp': b, 'GpEn': c, 'GpEp': d}, ignore_index=True)

scs  = condSums/100

# setup df for condition means for each sub
for n in range(1,subNum + 1):
    rn = n - 1
    a2 = GnEn_means.iloc[rn]
    b2 = GnEp_means.iloc[rn]
    c2 = GpEn_means.iloc[rn]
    d2 = GpEp_means.iloc[rn]
    condMeans = condMeans.append({'GnEn': a2, 'GnEp': b2, 'GpEn': c2, 'GpEp': d2}, ignore_index=True)
cms = condMeans

In [ ]:
# 4D plot of conds
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

x = cms["GnEn"]
y = cms["GnEp"]
z = cms["GpEn"]
c = cms["GpEp"]

img = ax.scatter(x, y, z, c=c, cmap=plt.viridis())
fig.colorbar(img)
plt.show()
#fig.savefig('allsubs_4d_scatterplot.pdf')

## K-Means Clustering

In [ ]:
km5 = KMeans(init='k-means++', n_clusters=5)
km5.fit(cms)
y_kmeans5 = km5.predict(cms)

## DF config and reordering

In [ ]:
subList = thresh80[["sub"]]
subList = subList.reset_index(drop=True)
cluster_model5 = pd.DataFrame(y_kmeans5, columns=['clust'])
clustList5 = pd.concat([subList, cluster_model5, cms], axis=1)

In [ ]:
allDF = pd.concat([clustList5, rmet, ht], axis=1)
allDF.shape

In [ ]:
allHT = allDF.copy()
allHT = allHT.dropna()
allHT["ht"] = pd.to_numeric(allHT["ht"])
allHT.shape

In [ ]:
allHTE = pd.concat([clustList5, rmet, hte], axis=1)
allHTE = allHTE.dropna()
allHTE["ht"] = pd.to_numeric(allHTE["ht"])
allHTE.shape

In [ ]:
# Means by cluster
clust0a = allHTE[allHTE["clust"] == 0]
rc0 = clust0a["WC_Avg"]
hc0 = clust0a["ht"]
c0_rmean = round(rc0.mean(),2)
c0_hmean = round(hc0.mean(),2)
clust1a = allHTE[allHTE["clust"] == 1]
rc1 = clust1a["WC_Avg"]
hc1 = clust1a["ht"]
c1_rmean = round(rc1.mean(),2)
c1_hmean = round(hc1.mean(),2)
clust2a = allHTE[allHTE["clust"] == 2]
rc2 = clust2a["WC_Avg"]
hc2 = clust2a["ht"]
c2_rmean = round(rc2.mean(),2)
c2_hmean = round(hc2.mean(),2)
clust3a = allHTE[allHTE["clust"] == 3]
rc3 = clust3a["rmet"]
hc3 = clust3a["ht"]
c3_rmean = round(rc3.mean(),2)
c3_hmean = round(hc3.mean(),2)
clust4a = allHTE[allHTE["clust"] == 4]
rc4 = clust4a["WC_Avg"]
hc4 = clust4a["ht"]
c4_rmean = round(rc4.mean(),2)
c4_hmean = round(hc4.mean(),2)

print("clust1: WC mean = " + str(c1_rmean) + ", ht mean = " + str(c1_hmean))
print("clust2: WC mean = " + str(c2_rmean) + ", ht mean = " + str(c2_hmean))
print("clust3: WC mean = " + str(c3_rmean) + ", ht mean = " + str(c3_hmean))
print("clust4: WC mean = " + str(c4_rmean) + ", ht mean = " + str(c4_hmean))
print("clust0: WC mean = " + str(c0_rmean) + ", ht mean = " + str(c0_hmean))

In [ ]:
# Means by cluster
clust0 = allDF[allDF["clust"] == 0]
clust0a = allHT[allHT["clust"] == 0]
rc0 = clust0["rmet"]
hc0 = clust0a["ht"]
c0_rmean = round(rc0.mean(),2)
c0_hmean = round(hc0.mean(),2)
clust1 = allDF[allDF["clust"] == 1]
clust1a = allHT[allHT["clust"] == 1]
rc1 = clust1["rmet"]
hc1 = clust1a["ht"]
c1_rmean = round(rc1.mean(),2)
c1_hmean = round(hc1.mean(),2)
clust2 = allDF[allDF["clust"] == 2]
clust2a = allHT[allHT["clust"] == 2]
rc2 = clust2["rmet"]
hc2 = clust2a["ht"]
c2_rmean = round(rc2.mean(),2)
c2_hmean = round(hc2.mean(),2)
clust3 = allDF[allDF["clust"] == 3]
clust3a = allHT[allHT["clust"] == 3]
rc3 = clust3["rmet"]
hc3 = clust3a["ht"]
c3_rmean = round(rc3.mean(),2)
c3_hmean = round(hc3.mean(),2)
clust4 = allDF[allDF["clust"] == 4]
clust4a = allHT[allHT["clust"] == 4]
rc4 = clust4["rmet"]
hc4 = clust4a["ht"]
c4_rmean = round(rc4.mean(),2)
c4_hmean = round(hc4.mean(),2)
rmeansdict = {
  "0": c0_rmean,
  "1": c1_rmean,
  "2": c2_rmean,
  "3": c3_rmean,
  "4": c4_rmean
}
print("clust1: rmet mean = " + str(c1_rmean) + ", ht mean = " + str(c1_hmean))
print("clust2: rmet mean = " + str(c2_rmean) + ", ht mean = " + str(c2_hmean))
print("clust3: rmet mean = " + str(c3_rmean) + ", ht mean = " + str(c3_hmean))
print("clust4: rmet mean = " + str(c4_rmean) + ", ht mean = " + str(c4_hmean))
print("clust0: rmet mean = " + str(c0_rmean) + ", ht mean = " + str(c0_hmean))

In [ ]:
# Copy dictionary
rMeansDict = rmeansdict.copy()
origMeansList = list(rMeansDict.values())
newMeansList = []
newMeansDict = {}
compMeansDict = {}

for cm in range(len(origMeansList)):
    currMin = min(origMeansList)
    newMeansDict[cm] = currMin
    origNum = list(rMeansDict.values()).index(currMin)
    compMeansDict[origNum] = cm
    origMeansList.remove(currMin)

In [ ]:
clustList5 = clustList5.replace({"clust": compMeansDict})
clustList5["clust"] += 1
new_clusts = list(clustList5["clust"])
allDF = allDF.replace({"clust": compMeansDict})
allDF["clust"] += 1
allHT = allDF.copy()
allHT = allHT.dropna()
allHT["ht"] = pd.to_numeric(allHT["ht"])

In [ ]:
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

x = cms["GnEn"]
y = cms["GnEp"]
z = cms["GpEn"]
c = cms["GpEp"]

img = ax.scatter(x, y, z, c=new_clusts, cmap=plt.viridis())
legend1 = ax.legend(*img.legend_elements(), bbox_to_anchor=(1.25, 1), loc="upper right", title="Clusters")
ax.add_artist(legend1)
ax.tick_params(axis ='x', rotation =45)
ax.tick_params(axis ='y', rotation =-45)
plt.xlim(-1, 1)
plt.ylim(-1, 1)
plt.show()
#fig.savefig('allsubs_kmeans_scatterplot.pdf')

### Avg Cluster Responses

In [ ]:
clst5_melt = pd.melt(clustList5,('sub','clust'),var_name='cond',value_name='rating')
g = sns.catplot(x="cond", y="rating", kind='bar', ci=68, col="clust", col_wrap=5, data=clst5_melt)
plt.tight_layout()
#plt.savefig('avg_resp_barplot.pdf')

In [ ]:
# Means by cluster
clust1 = allDF[allDF["clust"] == 1]
clust1a = allHT[allHT["clust"] == 1]
c1_num = len(clust1)
c1a_num = len(clust1a)
print("Number of c1-rmet subs: " + str(c1_num))
print("Number of c1-ht subs: " + str(c1a_num))
rc1 = clust1["rmet"]
hc1 = clust1a["ht"]
c1_rmean = round(rc1.mean(),2)
c1_hmean = round(hc1.mean(),2)
c1_rsem = round(stats.sem(rc1),2)
c1_hsem = round(stats.sem(hc1),2)
print("clust1: rmet mean = " + str(c1_rmean) + ", ht mean = " + str(c1_hmean))
print("clust1: rmet sem = " + str(c1_rsem) + ", ht sem = " + str(c1_hsem))
###
clust2 = allDF[allDF["clust"] == 2]
clust2a = allHT[allHT["clust"] == 2]
c2_num = len(clust2)
c2a_num = len(clust2a)
print("Number of c2-rmet subs: " + str(c2_num))
print("Number of c2-ht subs: " + str(c2a_num))
rc2 = clust2["rmet"]
hc2 = clust2a["ht"]
c2_rmean = round(rc2.mean(),2)
c2_hmean = round(hc2.mean(),2)
c2_rsem = round(stats.sem(rc2),2)
c2_hsem = round(stats.sem(hc2),2)
print("clust2: rmet mean = " + str(c2_rmean) + ", ht mean = " + str(c2_hmean))
print("clust2: rmet sem = " + str(c2_rsem) + ", ht sem = " + str(c2_hsem))
###
clust3 = allDF[allDF["clust"] == 3]
clust3a = allHT[allHT["clust"] == 3]
c3_num = len(clust3)
c3a_num = len(clust3a)
print("Number of c3-rmet subs: " + str(c3_num))
print("Number of c3-ht subs: " + str(c3a_num))
rc3 = clust3["rmet"]
hc3 = clust3a["ht"]
c3_rmean = round(rc3.mean(),2)
c3_hmean = round(hc3.mean(),2)
c3_rsem = round(stats.sem(rc3),2)
c3_hsem = round(stats.sem(hc3),2)
print("clust3: rmet mean = " + str(c3_rmean) + ", ht mean = " + str(c3_hmean))
print("clust3: rmet sem = " + str(c3_rsem) + ", ht sem = " + str(c3_hsem))
###
clust4 = allDF[allDF["clust"] == 4]
clust4a = allHT[allHT["clust"] == 4]
c4_num = len(clust4)
c4a_num = len(clust4a)
print("Number of c4-rmet subs: " + str(c4_num))
print("Number of c4-ht subs: " + str(c4a_num))
rc4 = clust4["rmet"]
hc4 = clust4a["ht"]
c4_rmean = round(rc4.mean(),2)
c4_hmean = round(hc4.mean(),2)
c4_rsem = round(stats.sem(rc4),2)
c4_hsem = round(stats.sem(hc4),2)
print("clust4: rmet mean = " + str(c4_rmean) + ", ht mean = " + str(c4_hmean))
print("clust4: rmet sem = " + str(c4_rsem) + ", ht sem = " + str(c4_hsem))
###
clust5 = allDF[allDF["clust"] == 5]
clust5a = allHT[allHT["clust"] == 5]
c5_num = len(clust5)
c5a_num = len(clust5a)
print("Number of c5-rmet subs: " + str(c5_num))
print("Number of c5-ht subs: " + str(c5a_num))
rc5 = clust5["rmet"]
hc5 = clust5a["ht"]
c5_rmean = round(rc5.mean(),2)
c5_hmean = round(hc5.mean(),2)
c5_rsem = round(stats.sem(rc5),2)
c5_hsem = round(stats.sem(hc5),2)
print("clust5: rmet mean = " + str(c5_rmean) + ", ht mean = " + str(c5_hmean))
print("clust5: rmet sem = " + str(c5_rsem) + ", ht sem = " + str(c5_hsem))
###
print("Total # of rmet subs: " + str(sum([c1_num,c2_num,c3_num,c4_num,c5_num])))
print("Total # of ht subs: " + str(sum([c1a_num,c2a_num,c3a_num,c4a_num,c5a_num])))
rmeansdict = {
  "1": c1_rmean,
  "2": c2_rmean,
  "3": c3_rmean,
  "4": c4_rmean,
  "5": c5_rmean
}

In [ ]:
rnonstrat = allDF.loc[(allDF["clust"] == 1) | (allDF["clust"] == 2), "rmet"]
rstrat = allDF.loc[(allDF["clust"] == 3) | (allDF["clust"] == 4) | (allDF["clust"] == 5), "rmet"]
hnonstrat = allDF.loc[(allDF["clust"] == 1) | (allDF["clust"] == 2), "ht"]
hstrat = allDF.loc[(allDF["clust"] == 3) | (allDF["clust"] == 4) | (allDF["clust"] == 5), "ht"]

In [ ]:
print("Non-strategy, RMET")
print(rnonstrat.mean())
print(rnonstrat.std())
print("Strategy, RMET")
print(rstrat.mean())
print(rstrat.std())
print("Non-strategy, HT")
print(hnonstrat.mean())
print(hnonstrat.std())
print("Strategy, HT")
print(hstrat.mean())
print(hstrat.std())

### K-Means - RMET x cluster

In [ ]:
g = sns.catplot(x="clust", y="rmet", kind='bar', data=allDF, ci=68)
g.set(xlabel='Cluster', ylabel='Avg RMET Score')
plt.tight_layout()
#plt.savefig('rmet_clust_barplot.pdf')

### K-Means - HT x cluster

In [ ]:
g = sns.catplot(x="clust", y="ht", kind='bar', data=allHT, ci=68)
g.set(xlabel='Cluster', ylabel='Avg Hinting Task Score')
plt.tight_layout()
#plt.savefig('ht_clust_barplot.pdf')

## RMET x HT Correlation

In [ ]:
g = sns.lmplot(data=allHT, x="ht", y="rmet", ci=68)
stats.pearsonr(allHT["ht"],allHT["rmet"])
g.set(xlabel='Avg Hinting Task Score', ylabel='Avg RMET Score')
plt.tight_layout()
stats.pearsonr(allHT["ht"],allHT["rmet"])
#plt.savefig('rmet_ht_scatterplot.pdf')

In [ ]:
model = ols("allHT[\"ht\"] ~ allHT[\"rmet\"]", allHT).fit()
print(model.summary())
stats.pearsonr(allHT["ht"],allHT["rmet"])

## Strategy Scores

In [ ]:
# Difference sum of squares
vals = pd.DataFrame(columns=['intDiff', 'gazeDiff', 'exprDiff'])
subCount = len(allDF["sub"])
subList = allDF["sub"]
clstList = allDF["clust"]
i1 = -1
i2 = 0
i3 = 0
i4 = 1
g1 = -1
g2 = -1
g3 = 1
g4 = 1
e1 = -1
e2 = 1
e3 = -1
e4 = 1
for s in range(0,subCount):
    clst = clstList[s]
    currSub = subList[s]
    currRow = cms.iloc[s]
    c1 = currRow[0]
    c2 = currRow[1]
    c3 = currRow[2]
    c4 = currRow[3]
    iv1 = (i1-c1)**2
    iv2 = (i2-c2)**2
    iv3 = (i3-c3)**2
    iv4 = (i4-c4)**2
    ivSum = (iv1+iv2+iv3+iv4)
    ivFinal = round(ivSum,2)
    gv1 = (g1-c1)**2
    gv2 = (g2-c2)**2
    gv3 = (g3-c3)**2
    gv4 = (g4-c4)**2
    gvSum = (gv1+gv2+gv3+gv4)
    gvFinal = round(gvSum,2)
    ev1 = (e1-c1)**2
    ev2 = (e2-c2)**2
    ev3 = (e3-c3)**2
    ev4 = (e4-c4)**2
    evSum = (ev1+ev2+ev3+ev4)
    evFinal = round(evSum,2)
    tVals = [ivFinal,gvFinal,evFinal]
    tVals = pd.DataFrame(tVals).T
    tVals.columns = ['intDiff','gazeDiff','exprDiff']
    vals = pd.concat([vals, tVals])
    vals = vals.reset_index(drop=True)

In [ ]:
incallDF = pd.concat([allDF,vals],axis=1)
incallHT = pd.concat([allHT,vals],axis=1).dropna()
melt_incallDF = pd.melt(incallDF,('sub','clust','GnEn','GnEp','GpEn','GpEp','rmet','ht'),var_name='respType',value_name='val')
melt_incallHT = pd.melt(incallHT,('sub','clust','GnEn','GnEp','GpEn','GpEp','rmet','ht'),var_name='respType',value_name='val')
#incallDF.to_excel("diffScores.xlsx")

In [ ]:
c1_incallDF = incallDF[incallDF["clust"] == 1]
c2_incallDF = incallDF[incallDF["clust"] == 2]
c3_incallDF = incallDF[incallDF["clust"] == 3]
c4_incallDF = incallDF[incallDF["clust"] == 4]
c5_incallDF = incallDF[incallDF["clust"] == 5]

c1_incallHT = incallHT[incallHT["clust"] == 1]
c2_incallHT = incallHT[incallHT["clust"] == 2]
c3_incallHT = incallHT[incallHT["clust"] == 3]
c4_incallHT = incallHT[incallHT["clust"] == 4]
c5_incallHT = incallHT[incallHT["clust"] == 5]

## Hinting Task Scatter Plots

In [ ]:
g = sns.lmplot(data=incallHT, x="ht", y="intDiff", ci=68)
g.set(xlabel='Avg Hinting Task Score', ylabel='Integrator Difference Score')
plt.tight_layout()
stats.pearsonr(incallHT["ht"],incallHT["intDiff"])
#plt.savefig('ht_int_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallHT[\"ht\"] ~ incallHT[\"intDiff\"]", incallHT).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=incallHT, x="ht", y="gazeDiff", ci=68)
g.set(xlabel='Avg Hinting Task Score', ylabel='Gaze Difference Score')
plt.tight_layout()
stats.pearsonr(incallHT["ht"],incallHT["gazeDiff"])
#plt.savefig('ht_gaze_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallHT[\"ht\"] ~ incallHT[\"gazeDiff\"]", incallHT).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=incallHT, x="ht", y="exprDiff", ci=68)
g.set(xlabel='Avg Hinting Task Score', ylabel='Expression Difference Score')
plt.tight_layout()
stats.pearsonr(incallHT["ht"],incallHT["exprDiff"])
#plt.savefig('ht_expr_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallHT[\"ht\"] ~ incallHT[\"exprDiff\"]", incallHT).fit()

# Print the summary
print(model.summary())

## RMET Scatter Plots

In [ ]:
g = sns.lmplot(data=incallDF, x="rmet", y="intDiff", ci=68)
g.set(xlabel='Avg RMET Score', ylabel='Integrator Difference Score')
plt.tight_layout()
stats.pearsonr(incallDF["rmet"],incallDF["intDiff"])
#plt.savefig('rmet_int_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallDF[\"rmet\"] ~ incallDF[\"intDiff\"]", incallDF).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=incallDF, x="rmet", y="gazeDiff", ci=68)
g.set(xlabel='Avg RMET Score', ylabel='Gaze Difference Score')
plt.tight_layout()
stats.pearsonr(incallDF["rmet"],incallDF["gazeDiff"])
#plt.savefig('rmet_gaze_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallDF[\"rmet\"] ~ incallDF[\"gazeDiff\"]", incallDF).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=incallDF, x="rmet", y="exprDiff", ci=68)
g.set(xlabel='Avg RMET Score', ylabel='Expression Difference Score')
plt.tight_layout()
stats.pearsonr(incallDF["rmet"],incallDF["exprDiff"])
#plt.savefig('rmet_expr_scatterplot.pdf')

In [ ]:
# Fit the model
model = ols("incallDF[\"rmet\"] ~ incallDF[\"exprDiff\"]", incallDF).fit()

# Print the summary
print(model.summary())

In [ ]:
c1_int = stats.pearsonr(c1_incallHT["ht"],c1_incallHT["intDiff"])
print("Clust 1 HTxIntegrator, r = " + str(round(c1_int[0],2)) + ", p = " + str(round(c1_int[1],2)))
c1_gaze = stats.pearsonr(c1_incallHT["ht"],c1_incallHT["gazeDiff"])
print("Clust 1 HTxGaze, r = " + str(round(c1_gaze[0],2)) + ", p = " + str(round(c1_gaze[1],2)))
c1_expr = stats.pearsonr(c1_incallHT["ht"],c1_incallHT["exprDiff"])
print("Clust 1 HTxExpression, r = " + str(round(c1_expr[0],2)) + ", p = " + str(round(c1_expr[1],2)))
print("+++++")
c2_int = stats.pearsonr(c2_incallHT["ht"],c2_incallHT["intDiff"])
print("Clust 2 HTxIntegrator, r = " + str(round(c2_int[0],2)) + ", p = " + str(round(c2_int[1],2)))
c2_gaze = stats.pearsonr(c2_incallHT["ht"],c2_incallHT["gazeDiff"])
print("Clust 2 HTxGaze, r = " + str(round(c2_gaze[0],2)) + ", p = " + str(round(c2_gaze[1],2)))
c2_expr = stats.pearsonr(c2_incallHT["ht"],c2_incallHT["exprDiff"])
print("Clust 2 HTxExpression, r = " + str(round(c2_expr[0],2)) + ", p = " + str(round(c2_expr[1],2)))
print("+++++")
c3_int = stats.pearsonr(c3_incallHT["ht"],c3_incallHT["intDiff"])
print("Clust 3 HTxIntegrator, r = " + str(round(c3_int[0],2)) + ", p = " + str(round(c3_int[1],2)))
c3_gaze = stats.pearsonr(c3_incallHT["ht"],c3_incallHT["gazeDiff"])
print("Clust 3 HTxGaze, r = " + str(round(c3_gaze[0],2)) + ", p = " + str(round(c3_gaze[1],2)))
c3_expr = stats.pearsonr(c3_incallHT["ht"],c3_incallHT["exprDiff"])
print("Clust 3 HTxExpression, r = " + str(round(c3_expr[0],2)) + ", p = " + str(round(c3_expr[1],2)))
print("+++++")
c4_int = stats.pearsonr(c4_incallHT["ht"],c4_incallHT["intDiff"])
print("Clust 4 HTxIntegrator, r = " + str(round(c4_int[0],2)) + ", p = " + str(round(c4_int[1],2)))
c4_gaze = stats.pearsonr(c4_incallHT["ht"],c4_incallHT["gazeDiff"])
print("Clust 4 HTxGaze, r = " + str(round(c4_gaze[0],2)) + ", p = " + str(round(c4_gaze[1],2)))
c4_expr = stats.pearsonr(c4_incallHT["ht"],c4_incallHT["exprDiff"])
print("Clust 4 HTxExpression, r = " + str(round(c4_expr[0],2)) + ", p = " + str(round(c4_expr[1],2)))
print("+++++")
c5_int = stats.pearsonr(c5_incallHT["ht"],c5_incallHT["intDiff"])
print("Clust 5 HTxIntegrator, r = " + str(round(c5_int[0],2)) + ", p = " + str(round(c5_int[1],2)))
c5_gaze = stats.pearsonr(c5_incallHT["ht"],c5_incallHT["gazeDiff"])
print("Clust 5 HTxGaze, r = " + str(round(c5_gaze[0],2)) + ", p = " + str(round(c5_gaze[1],2)))
c5_expr = stats.pearsonr(c5_incallHT["ht"],c5_incallHT["exprDiff"])
print("Clust 5 HTxExpression, r = " + str(round(c5_expr[0],2)) + ", p = " + str(round(c5_expr[1],2)))

In [ ]:
rc1_int = stats.pearsonr(c1_incallDF["rmet"],c1_incallDF["intDiff"])
print("Clust 1 rmetxIntegrator, r = " + str(round(rc1_int[0],2)) + ", p = " + str(round(rc1_int[1],2)))
rc1_gaze = stats.pearsonr(c1_incallDF["rmet"],c1_incallDF["gazeDiff"])
print("Clust 1 rmetxGaze, r = " + str(round(rc1_gaze[0],2)) + ", p = " + str(round(rc1_gaze[1],2)))
rc1_expr = stats.pearsonr(c1_incallDF["rmet"],c1_incallDF["exprDiff"])
print("Clust 1 rmetxExpression, r = " + str(round(rc1_expr[0],2)) + ", p = " + str(round(rc1_expr[1],2)))
print("+++++")
rc2_int = stats.pearsonr(c2_incallDF["rmet"],c2_incallDF["intDiff"])
print("Clust 2 rmetxIntegrator, r = " + str(round(rc2_int[0],2)) + ", p = " + str(round(rc2_int[1],2)))
rc2_gaze = stats.pearsonr(c2_incallDF["rmet"],c2_incallDF["gazeDiff"])
print("Clust 2 rmetxGaze, r = " + str(round(rc2_gaze[0],2)) + ", p = " + str(round(rc2_gaze[1],2)))
rc2_expr = stats.pearsonr(c2_incallDF["rmet"],c2_incallDF["exprDiff"])
print("Clust 2 rmetxExpression, r = " + str(round(rc2_expr[0],2)) + ", p = " + str(round(rc2_expr[1],2)))
print("+++++")
rc3_int = stats.pearsonr(c3_incallDF["rmet"],c3_incallDF["intDiff"])
print("Clust 3 rmetxIntegrator, r = " + str(round(rc3_int[0],2)) + ", p = " + str(round(rc3_int[1],2)))
rc3_gaze = stats.pearsonr(c3_incallDF["rmet"],c3_incallDF["gazeDiff"])
print("Clust 3 rmetxGaze, r = " + str(round(rc3_gaze[0],2)) + ", p = " + str(round(rc3_gaze[1],2)))
rc3_expr = stats.pearsonr(c3_incallDF["rmet"],c3_incallDF["exprDiff"])
print("Clust 3 rmetxExpression, r = " + str(round(rc3_expr[0],2)) + ", p = " + str(round(rc3_expr[1],2)))
print("+++++")
rc4_int = stats.pearsonr(c4_incallDF["rmet"],c4_incallDF["intDiff"])
print("Clust 4 rmetxIntegrator, r = " + str(round(rc4_int[0],2)) + ", p = " + str(round(rc4_int[1],2)))
rc4_gaze = stats.pearsonr(c4_incallDF["rmet"],c4_incallDF["gazeDiff"])
print("Clust 4 rmetxGaze, r = " + str(round(rc4_gaze[0],2)) + ", p = " + str(round(rc4_gaze[1],2)))
rc4_expr = stats.pearsonr(c4_incallDF["rmet"],c4_incallDF["exprDiff"])
print("Clust 4 rmetxExpression, r = " + str(round(rc4_expr[0],2)) + ", p = " + str(round(rc4_expr[1],2)))
print("+++++")
rc5_int = stats.pearsonr(c5_incallDF["rmet"],c5_incallDF["intDiff"])
print("Clust 5 rmetxIntegrator, r = " + str(round(rc5_int[0],2)) + ", p = " + str(round(rc5_int[1],2)))
rc5_gaze = stats.pearsonr(c5_incallDF["rmet"],c5_incallDF["gazeDiff"])
print("Clust 5 rmetxGaze, r = " + str(round(rc5_gaze[0],2)) + ", p = " + str(round(rc5_gaze[1],2)))
rc5_expr = stats.pearsonr(c5_incallDF["rmet"],c5_incallDF["exprDiff"])
print("Clust 5 rmetxExpression, r = " + str(round(rc5_expr[0],2)) + ", p = " + str(round(rc5_expr[1],2)))

## Median splits

In [ ]:
allDF_med = statistics.median(allDF["rmet"])
lwr_allDF = allDF[allDF.rmet <= allDF_med]
rmet_lwr = lwr_allDF.drop(columns=['rmet', 'ht'])
gtr_allDF = allDF[allDF.rmet > allDF_med]
rmet_gtr = gtr_allDF.drop(columns=['rmet', 'ht'])
rmet_gtr_melt = pd.melt(rmet_gtr,('sub','clust'),var_name='cond',value_name='rating')
rmet_lwr_melt = pd.melt(rmet_lwr,('sub','clust'),var_name='cond',value_name='rating')

In [ ]:
g = sns.catplot(x="clust", y="rmet", kind='bar', data=lwr_allDF)
g.set(xlabel='Cluster', ylabel='Avg RMET Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_rmet_clust_barplot.png')

In [ ]:
g = sns.catplot(x="clust", y="rmet", kind='bar', data=gtr_allDF)
g.set(xlabel='Cluster', ylabel='Avg RMET Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_rmet_clust_barplot.png')

In [ ]:
g = sns.catplot(x="cond", y="rating", kind='bar', col="clust", col_wrap=5, data=rmet_lwr_melt)
plt.tight_layout()
#plt.savefig('medsplt_lwr50_conds_barplot.png')

In [ ]:
g = sns.catplot(x="cond", y="rating", kind='bar', col="clust", col_wrap=5, data=rmet_gtr_melt)
plt.tight_layout()
#plt.savefig('medsplt_gtr50_conds_barplot.png')

In [ ]:
allHT_med = statistics.median(allHT["ht"])
lwr_allHT = allHT[allHT.ht <= allHT_med]
ht_lwr = lwr_allHT.drop(columns=['rmet', 'ht'])
gtr_allHT = allHT[allHT.ht > allHT_med]
ht_gtr = lwr_allHT.drop(columns=['rmet', 'ht'])
ht_gtr_melt = pd.melt(ht_gtr,('sub','clust'),var_name='cond',value_name='rating')
ht_lwr_melt = pd.melt(ht_lwr,('sub','clust'),var_name='cond',value_name='rating')

In [ ]:
g = sns.catplot(x="clust", y="ht", kind='bar', data=lwr_allHT)
g.set(xlabel='Cluster', ylabel='Avg Hinting Task Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_ht_clust_barplot.png')

In [ ]:
g = sns.catplot(x="clust", y="ht", kind='bar', data=gtr_allHT)
g.set(xlabel='Cluster', ylabel='Avg Hinting Task Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_ht_clust_barplot.png')

In [ ]:
# Means by cluster
print("Lower Split - RMET & HT")
l_rclust1 = lwr_allDF[lwr_allDF["clust"] == 1]
l_hclust1 = lwr_allHT[lwr_allHT["clust"] == 1]
l_rc1 = l_rclust1["rmet"]
l_hc1 = l_hclust1["ht"]
l_c1_rmean = round(l_rc1.mean(),2)
l_c1_hmean = round(l_hc1.mean(),2)
print("clust1: rmet mean = " + str(l_c1_rmean) + ", ht mean = " + str(l_c1_hmean))
l_rc1_num = len(l_rc1)
l_hc1_num = len(l_hc1)
print("Number of c1-rmet subs: " + str(l_rc1_num))
print("Number of c1-ht subs: " + str(l_hc1_num))
###
l_rclust2 = lwr_allDF[lwr_allDF["clust"] == 2]
l_hclust2 = lwr_allHT[lwr_allHT["clust"] == 2]
l_rc2 = l_rclust2["rmet"]
l_hc2 = l_hclust2["ht"]
l_c2_rmean = round(l_rc2.mean(),2)
l_c2_hmean = round(l_hc2.mean(),2)
print("clust2: rmet mean = " + str(l_c2_rmean) + ", ht mean = " + str(l_c2_hmean))
l_rc2_num = len(l_rc2)
l_hc2_num = len(l_hc2)
print("Number of c2-rmet subs: " + str(l_rc2_num))
print("Number of c2-ht subs: " + str(l_hc2_num))
###
l_rclust3 = lwr_allDF[lwr_allDF["clust"] == 3]
l_hclust3 = lwr_allHT[lwr_allHT["clust"] == 3]
l_rc3 = l_rclust3["rmet"]
l_hc3 = l_hclust3["ht"]
l_c3_rmean = round(l_rc3.mean(),2)
l_c3_hmean = round(l_hc3.mean(),2)
print("clust3: rmet mean = " + str(l_c3_rmean) + ", ht mean = " + str(l_c3_hmean))
l_rc3_num = len(l_rc3)
l_hc3_num = len(l_hc3)
print("Number of c3-rmet subs: " + str(l_rc3_num))
print("Number of c3-ht subs: " + str(l_hc3_num))
###
l_rclust4 = lwr_allDF[lwr_allDF["clust"] == 4]
l_hclust4 = lwr_allHT[lwr_allHT["clust"] == 4]
l_rc4 = l_rclust4["rmet"]
l_hc4 = l_hclust4["ht"]
l_c4_rmean = round(l_rc4.mean(),2)
l_c4_hmean = round(l_hc4.mean(),2)
print("clust4: rmet mean = " + str(l_c4_rmean) + ", ht mean = " + str(l_c4_hmean))
l_rc4_num = len(l_rc4)
l_hc4_num = len(l_hc4)
print("Number of c4-rmet subs: " + str(l_rc4_num))
print("Number of c4-ht subs: " + str(l_hc4_num))
###
l_rclust5 = lwr_allDF[lwr_allDF["clust"] == 5]
l_hclust5 = lwr_allHT[lwr_allHT["clust"] == 5]
l_rc5 = l_rclust5["rmet"]
l_hc5 = l_hclust5["ht"]
l_c5_rmean = round(l_rc5.mean(),2)
l_c5_hmean = round(l_hc5.mean(),2)
print("clust5: rmet mean = " + str(l_c5_rmean) + ", ht mean = " + str(l_c5_hmean))
l_rc5_num = len(l_rc5)
l_hc5_num = len(l_hc5)
print("Number of c5-rmet subs: " + str(l_rc5_num))
print("Number of c5-ht subs: " + str(l_hc5_num))
###
print("Total # of rmet subs: " + str(sum([l_rc1_num,l_rc2_num,l_rc3_num,l_rc4_num,l_rc5_num])))
print("Total # of ht subs: " + str(sum([l_hc1_num,l_hc2_num,l_hc3_num,l_hc4_num,l_hc5_num])))

In [ ]:
# Means by cluster
print("Greater Split - RMET & HT")
g_rclust1 = gtr_allDF[gtr_allDF["clust"] == 1]
g_hclust1 = gtr_allHT[gtr_allHT["clust"] == 1]
g_rc1 = g_rclust1["rmet"]
g_hc1 = g_hclust1["ht"]
g_c1_rmean = round(g_rc1.mean(),2)
g_c1_hmean = round(g_hc1.mean(),2)
print("clust1: rmet mean = " + str(g_c1_rmean) + ", ht mean = " + str(g_c1_hmean))
g_rc1_num = len(g_rc1)
g_hc1_num = len(g_hc1)
print("Number of c1-rmet subs: " + str(g_rc1_num))
print("Number of c1-ht subs: " + str(g_hc1_num))
###
g_rclust2 = gtr_allDF[gtr_allDF["clust"] == 2]
g_hclust2 = gtr_allHT[gtr_allHT["clust"] == 2]
g_rc2 = g_rclust2["rmet"]
g_hc2 = g_hclust2["ht"]
g_c2_rmean = round(g_rc2.mean(),2)
g_c2_hmean = round(g_hc2.mean(),2)
print("clust2: rmet mean = " + str(g_c2_rmean) + ", ht mean = " + str(g_c2_hmean))
g_rc2_num = len(g_rc2)
g_hc2_num = len(g_hc2)
print("Number of c2-rmet subs: " + str(g_rc2_num))
print("Number of c2-ht subs: " + str(g_hc2_num))
###
g_rclust3 = gtr_allDF[gtr_allDF["clust"] == 3]
g_hclust3 = gtr_allHT[gtr_allHT["clust"] == 3]
g_rc3 = g_rclust3["rmet"]
g_hc3 = g_hclust3["ht"]
g_c3_rmean = round(g_rc3.mean(),2)
g_c3_hmean = round(g_hc3.mean(),2)
print("clust3: rmet mean = " + str(g_c3_rmean) + ", ht mean = " + str(g_c3_hmean))
g_rc3_num = len(g_rc3)
g_hc3_num = len(g_hc3)
print("Number of c3-rmet subs: " + str(g_rc3_num))
print("Number of c3-ht subs: " + str(g_hc3_num))
###
g_rclust4 = gtr_allDF[gtr_allDF["clust"] == 4]
g_hclust4 = gtr_allHT[gtr_allHT["clust"] == 4]
g_rc4 = g_rclust4["rmet"]
g_hc4 = g_hclust4["ht"]
g_c4_rmean = round(g_rc4.mean(),2)
g_c4_hmean = round(g_hc4.mean(),2)
print("clust4: rmet mean = " + str(g_c4_rmean) + ", ht mean = " + str(g_c4_hmean))
g_rc4_num = len(g_rc4)
g_hc4_num = len(g_hc4)
print("Number of c4-rmet subs: " + str(g_rc4_num))
print("Number of c4-ht subs: " + str(g_hc4_num))
###
g_rclust5 = gtr_allDF[gtr_allDF["clust"] == 5]
g_hclust5 = gtr_allHT[gtr_allHT["clust"] == 5]
g_rc5 = g_rclust5["rmet"]
g_hc5 = g_hclust5["ht"]
g_c5_rmean = round(g_rc5.mean(),2)
g_c5_hmean = round(g_hc5.mean(),2)
print("clust5: rmet mean = " + str(g_c5_rmean) + ", ht mean = " + str(g_c5_hmean))
g_rc5_num = len(g_rc5)
g_hc5_num = len(g_hc5)
print("Number of c5-rmet subs: " + str(g_rc5_num))
print("Number of c5-ht subs: " + str(g_hc5_num))
###
print("Total # of rmet subs: " + str(sum([g_rc1_num,g_rc2_num,g_rc3_num,g_rc4_num,g_rc5_num])))
print("Total # of ht subs: " + str(sum([g_hc1_num,g_hc2_num,g_hc3_num,g_hc4_num,g_hc5_num])))

In [ ]:
rmet_med = statistics.median(incallDF["rmet"])
lt_rmet = incallDF[incallDF.rmet <= rmet_med]
gt_rmet = incallDF[incallDF.rmet > rmet_med]

In [ ]:
g = sns.lmplot(data=lt_rmet, x="rmet", y="intDiff")
stats.pearsonr(lt_rmet["rmet"],lt_rmet["intDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Integrator Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_rmet_int_scatterplot.pdf')
stats.pearsonr(lt_rmet["rmet"],lt_rmet["intDiff"])

In [ ]:
# Fit the model
model = ols("lt_rmet[\"rmet\"] ~ lt_rmet[\"intDiff\"]", lt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_rmet, x="rmet", y="intDiff")
stats.pearsonr(gt_rmet["rmet"],gt_rmet["intDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Integrator Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_rmet_int_scatterplot.pdf')
stats.pearsonr(gt_rmet["rmet"],gt_rmet["intDiff"])

In [ ]:
# Fit the model
model = ols("gt_rmet[\"rmet\"] ~ gt_rmet[\"intDiff\"]", gt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=lt_rmet, x="rmet", y="gazeDiff")
stats.pearsonr(lt_rmet["rmet"],lt_rmet["gazeDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Gaze Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_rmet_gaze_scatterplot.pdf')
stats.pearsonr(lt_rmet["rmet"],lt_rmet["gazeDiff"])

In [ ]:
# Fit the model
model = ols("lt_rmet[\"rmet\"] ~ lt_rmet[\"gazeDiff\"]", lt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_rmet, x="rmet", y="gazeDiff")
stats.pearsonr(gt_rmet["rmet"],gt_rmet["gazeDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Gaze Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_rmet_gaze_scatterplot.pdf')
stats.pearsonr(gt_rmet["rmet"],gt_rmet["gazeDiff"])

In [ ]:
# Fit the model
model = ols("gt_rmet[\"rmet\"] ~ gt_rmet[\"gazeDiff\"]", gt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=lt_rmet, x="rmet", y="exprDiff")
stats.pearsonr(lt_rmet["rmet"],lt_rmet["exprDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Expression Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_rmet_expr_scatterplot.pdf')
stats.pearsonr(lt_rmet["rmet"],lt_rmet["exprDiff"])

In [ ]:
# Fit the model
model = ols("lt_rmet[\"rmet\"] ~ lt_rmet[\"exprDiff\"]", lt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_rmet, x="rmet", y="exprDiff")
stats.pearsonr(gt_rmet["rmet"],gt_rmet["exprDiff"])
g.set(xlabel='Avg RMET Score', ylabel='Expression Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_rmet_expr_scatterplot.pdf')
stats.pearsonr(gt_rmet["rmet"],gt_rmet["exprDiff"])

In [ ]:
# Fit the model
model = ols("gt_rmet[\"rmet\"] ~ gt_rmet[\"exprDiff\"]", gt_rmet).fit()

# Print the summary
print(model.summary())

In [ ]:
ht_med = statistics.median(incallHT["ht"])
lt_ht = incallHT[incallHT.ht <= ht_med]
gt_ht = incallHT[incallHT.ht > ht_med]

In [ ]:
print(rmet_med)
print(ht_med)

In [ ]:
g = sns.lmplot(data=lt_ht, x="ht", y="intDiff")
stats.pearsonr(lt_ht["ht"],lt_ht["intDiff"])
g.set(xlabel='Avg HT Score', ylabel='Integrator Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_ht_int_scatterplot.pdf')
stats.pearsonr(lt_ht["rmet"],lt_ht["intDiff"])

In [ ]:
# Fit the model
model = ols("lt_ht[\"rmet\"] ~ lt_ht[\"intDiff\"]", lt_ht).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_ht, x="ht", y="intDiff")
stats.pearsonr(gt_ht["ht"],gt_ht["intDiff"])
g.set(xlabel='Avg HT Score', ylabel='Integrator Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_ht_int_scatterplot.pdf')
stats.pearsonr(gt_ht["rmet"],gt_ht["intDiff"])

In [ ]:
# Fit the model
model = ols("gt_ht[\"rmet\"] ~ gt_ht[\"intDiff\"]", gt_ht).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=lt_ht, x="ht", y="gazeDiff")
stats.pearsonr(lt_ht["ht"],lt_ht["gazeDiff"])
g.set(xlabel='Avg HT Score', ylabel='Gaze Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_ht_gaze_scatterplot.pdf')
stats.pearsonr(lt_ht["rmet"],lt_ht["gazeDiff"])

In [ ]:
# Fit the model
model = ols("lt_ht[\"rmet\"] ~ lt_ht[\"gazeDiff\"]", lt_ht).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_ht, x="ht", y="gazeDiff")
stats.pearsonr(gt_ht["ht"],gt_ht["gazeDiff"])
g.set(xlabel='Avg HT Score', ylabel='Gaze Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_ht_gaze_scatterplot.pdf')
stats.pearsonr(gt_ht["rmet"],gt_ht["gazeDiff"])

In [ ]:
# Fit the model
model = ols("gt_ht[\"rmet\"] ~ gt_ht[\"gazeDiff\"]", gt_ht).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=lt_ht, x="ht", y="exprDiff")
stats.pearsonr(lt_ht["ht"],lt_ht["exprDiff"])
g.set(xlabel='Avg HT Score', ylabel='Expression Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_lwr50_ht_expr_scatterplot.pdf')
stats.pearsonr(lt_ht["rmet"],lt_ht["exprDiff"])

In [ ]:
# Fit the model
model = ols("lt_ht[\"rmet\"] ~ lt_ht[\"exprDiff\"]", lt_ht).fit()

# Print the summary
print(model.summary())

In [ ]:
g = sns.lmplot(data=gt_ht, x="ht", y="exprDiff")
stats.pearsonr(gt_ht["ht"],gt_ht["exprDiff"])
g.set(xlabel='Avg HT Score', ylabel='Expression Difference Score')
plt.tight_layout()
#plt.savefig('medsplt_gtr50_ht_expr_scatterplot.pdf')
stats.pearsonr(gt_ht["rmet"],gt_ht["exprDiff"])

In [ ]:
# Fit the model
model = ols("gt_ht[\"rmet\"] ~ gt_ht[\"exprDiff\"]", gt_ht).fit()

# Print the summary
print(model.summary())

## Strategy vs ambiguous

In [ ]:
# Copy dictionary
rMeansDict = rmeansdict.copy()

# Pull out two lowest clusters
key_list = list(rMeansDict.keys()) 
val_list = list(rMeansDict.values())
abVal = min(val_list)
ab = key_list[val_list.index(abVal)]
val_list.remove(abVal)
key_list.remove(ab)
flatVal = min(val_list)
flat = key_list[val_list.index(flatVal)]

# Ambiguous clusters
ambig = [int(ab),int(flat)]
print(ambig)

In [ ]:
# RMET
stratDF = incallDF[~incallDF.clust.isin(ambig)]
nostratDF = incallDF[incallDF.clust.isin(ambig)]

In [ ]:
rStrat = stratDF["rmet"]
rNostrat = nostratDF["rmet"]

In [ ]:
sns.lmplot(data=stratDF, x="rmet", y="intDiff")
stats.pearsonr(stratDF["rmet"],stratDF["intDiff"])

In [ ]:
sns.lmplot(data=nostratDF, x="rmet", y="intDiff")
stats.pearsonr(nostratDF["rmet"],nostratDF["intDiff"])

In [ ]:
# HT
stratHT = incallHT[~incallHT.clust.isin(ambig)]
nostratHT = incallHT[incallHT.clust.isin(ambig)]

In [ ]:
hStrat = stratHT["ht"]
hNostrat = nostratHT["ht"]

In [ ]:
sns.lmplot(data=stratHT, x="ht", y="intDiff")
stats.pearsonr(stratHT["ht"],stratHT["intDiff"])

In [ ]:
sns.lmplot(data=nostratHT, x="ht", y="intDiff")
stats.pearsonr(nostratHT["ht"],nostratHT["intDiff"])

In [ ]:
print(allDF["rmet"].max())
print(allDF["rmet"].mean())
print(allDF["rmet"].std())
print(allDF["rmet"].min())

In [ ]:
print(allHT["ht"].max())
print(allHT["ht"].mean())
print(allHT["ht"].std())
print(allHT["ht"].min())

## T-tests

In [ ]:
# RMET Analyses

# Flat vs Aware Biased
r_tstat1, r_pval1 = stats.ttest_ind(rc1, rc2, equal_var=False)
print("Flat vs Aware Biased")
if r_pval1 > 0.25:
    print("1.00")
else:
    #print(r_pval1)
    print(str(round(r_pval1,3)))
    print(str(round(r_pval1,3)*4))

# Strategy vs no-strategy
r_tstat2, r_pval2 = stats.ttest_ind(rStrat, rNostrat, equal_var=False)
print("Strategy vs no-strategy")
if r_pval2 > 0.25:
    print("1.00")
else:
    #print(r_tstat2)
    print(r_pval2)
    print(str(round(r_pval2,3)*4))
print(r_tstat2)
# Int vs Gaze
r_tstat3, r_pval3 = stats.ttest_ind(rc3, rc5, equal_var=False)
print("Int vs Gaze")
if r_pval3 > 0.25:
    print("1.00")
else:
    #print(r_pval3)
    print(r_pval3)
    print(str(round(r_pval3,3)*4))
print(r_tstat3)
# Int vs Expr
r_tstat4, r_pval4 = stats.ttest_ind(rc4, rc5, equal_var=False)
print("Int vs Expr")
if r_pval4 > 0.25:
    print("1.00")
else:
    #print(r_pval4)
    print(r_pval4)
    print(str(round(r_pval4,3)*4))
print(r_tstat4)

In [ ]:
# HT Analyses

# Flat vs Aware Biased
h_tstat1, h_pval1 = stats.ttest_ind(hc1, hc2, equal_var=False)
print("Flat vs Aware Biased")
if h_pval1 > 0.25:
    print("1.00")
else:
    #print(h_pval1)
    print(h_pval1)
    print(str(round(h_pval1,3)*4))
print(h_tstat1)
# Strategy vs no-strategy
h_tstat2, h_pval2 = stats.ttest_ind(hStrat, hNostrat, equal_var=False)
print("Strategy vs no-strategy")
if h_pval2 > 0.25:
    print("1.00")
else:
    #print(h_tstat2)
    print(h_pval2*4)
    print(str(round(h_pval2,3)*4))
print(h_tstat2)
# Int vs Gaze
h_tstat3, h_pval3 = stats.ttest_ind(hc3, hc5, equal_var=False)
print("Int vs Gaze")
if h_pval3 > 0.25:
    print("1.00")
else:
    #print(h_pval3)
    print(h_pval3)
    print(str(round(h_pval3,3)*4))
print(h_tstat3)
# Int vs Expr
h_tstat4, h_pval4 = stats.ttest_ind(hc4, hc5, equal_var=False)
print("Int vs Expr")
if h_pval4 > 0.25:
    print("1.00")
else:
    #print(h_pval4)
    print(h_pval4)
    print(str(round(h_pval4,3)*4))
print(h_tstat4)

In [ ]:
print("*** Script complete! ***")